In [1]:
from bertviz import head_view
import pandas as pd
import numpy as np
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch
import random
import re
import os

In [2]:
def get_questions(path):
    '''
        Read in all the questions with their ids from a specific path
    '''

    questions = {}
    for root, dirs, files in os.walk(path):
        for file in files:
            if file=='context.txt':
                with open(os.path.join(root,file)) as f:
                    q_full = f.read().split('<br>')
                    q_text = q_full[2]
                    q_title = q_full[0]
                    q_context = ' '.join([x for x in re.split("[?.!;]", q_text) if x!=""][-3:])
                    # Strip off newline and tab characters
                    q_context = q_context.replace('\n', '').replace('\t', '')
                    q_context = q_context + " " + q_title
                    questions[root.split('/')[-1]] = q_context

    return questions

In [3]:
def find_context_full(ind, df):
    '''
    Return a reliable context for every sentence, instead of one of 3 possible
    things which might confuse the downstream model
    '''

    split_ind = ind.split('-')
    context = df.loc[(df['Post.ID']==split_ind[0]) & \
                     (df['Reply.ID']==split_ind[1]) & \
                     (df['Sent.Num']!=split_ind[2]), 'Sentence'].values.tolist()
    context = " ".join(context)

    return context

In [4]:
def find_reply(ind, df):
    '''
    Return a reliable context for every sentence, instead of one of 3 possible
    things which might confuse the downstream model
    '''

    split_ind = ind.split('-')
    context = df.loc[(df['Post.ID']==split_ind[0]) & \
                     (df['Reply.ID']==split_ind[1]), 'Sentence'].values.tolist()
    context = " ".join(context)

    return context

In [5]:
%%javascript
require.config({
  paths: {
      d3: '//cdnjs.cloudflare.com/ajax/libs/d3/3.4.8/d3.min',
      jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
  }
});

<IPython.core.display.Javascript object>

In [6]:
seed=45  # Not that this even matters if we're training on a separate machine

In [7]:
# Set random seeds for reproducibility on a specific machine
torch.backends.cudnn.benchmark = False
torch.backends.cudnn.deterministic = True
torch.manual_seed(seed)
torch.cuda.manual_seed(seed)
random.seed(seed)
np.random.seed(seed)
np.random.RandomState(seed)

RandomState(MT19937) at 0x1A3B47F678

In [8]:
pd.set_option('display.max_colwidth', None)

data = 'askparents'

pred_file = '../../preds/classifier_askparents_bert_dropout:0.1_lr_tr:1e-05_lr_cl:1e-05_wd:0_batch:32_finetune:True_query:True_context:False_seed:45_multigpu:True_labels:ds_frac:1_DEV.csv'

dev = pd.read_csv(pred_file, header=0, sep='\t')
dev_sentences = dev['Sentence'].tolist()
dev_labels_DS = dev['DS_Label'].values
dev_labels_Maj = dev['Majority_label'].values
dev['Pred_Label'] = dev['Pred_Label'].astype(int)
dev['Reply.ID'] = dev['Reply.ID'].astype(int).astype(str)
dev['Sent.Num'] = dev['Sent.Num'].astype(str)
dev_preds = dev['Pred_Label'].values
questions = get_questions('../../rawdata/' + data)
dev['Question'] = dev['ID'].apply(lambda x:questions[x.split('-')[0]])
dev['Context'] = dev['ID'].apply(lambda x: find_context_full(x, dev))

In [9]:
dev = dev.set_index('ID')

In [22]:
# Load the csv without questions just for comparison's sake
pred_file2 = '../../preds/classifier_askparents_bert_dropout:0.1_lr_tr:1e-05_lr_cl:1e-05_wd:0_batch:32_finetune:True_query:False_context:False_seed:45_multigpu:True_labels:ds_frac:1.csv'

dev2 = pd.read_csv(pred_file2, header=0, sep='\t')
dev2_sentences = dev2['Sentence'].tolist()
dev2_labels_DS = dev2['DS_Label'].values
dev2_labels_Maj = dev2['Majority_label'].values
dev2['Pred_Label'] = dev2['Pred_Label'].astype(int)
dev2['Reply.ID'] = dev2['Reply.ID'].astype(int).astype(str)
dev2['Sent.Num'] = dev2['Sent.Num'].astype(str)
dev2_preds = dev2['Pred_Label'].values
questions = get_questions('../../rawdata/' + data)
dev2['Question'] = dev2['ID'].apply(lambda x:questions[x.split('-')[0]])
dev2['Context'] = dev2['ID'].apply(lambda x: find_context_full(x, dev2))
dev2 = dev2.set_index('ID')

In [23]:
dev['NPred_Label'] = dev.index.map(lambda x: dev2.loc[x, 'Pred_Label'])
dev[(dev['Pred_Label']==0) & (dev['NPred_Label']==1)]

Majority_label  DS_Label  \
ID                                       
a8v90n-3-4                 0         0   
bp0iek-2-2                 0         0   
4xv4lf-2-2                 0         0   
dp6rdz-1.1-2               1         1   
be9axi-3-0                 1         1   
...                      ...       ...   
8kic2y-3-0                 1         1   
844azw-1-3                 0         0   
a8v90n-5-3                 0         0   
dp6rdz-5-2                 1         1   
98xghs-1-3                 1         1   

                                                                                                                                                                      Sentence  \
ID                                                                                                                                                                               
a8v90n-3-4                                  I ’m going to get her used you to sleeping in her crib soon so she can learn to settle back to sleep after each cycle on her own .   
bp0iek-2-2                                                                                                                                                  ” Then go settle .   
4xv4lf-2-2                                                                                                                                   And Big Bear needs a bear hug ! "   
dp6rdz-1.1-2                                                Stuff that melts in your mouth ( like chocolate without any candy coating or crackers ) is best for kids that age.   
be9axi-3-0                                                                                                                    I let my kids watch most things , PG and below .   
...                                                                                                                                                                        ...   
8kic2y-3-0                                                                                                                                         I 'd ask for $ 200 a week .   
844azw-1-3    When she would wait until the end of the routine and say she needed the bathroom again , I 'd just let her and then tuck her in with no fuss when she was done .   
a8v90n-5-3                                                                                                                          He should sleep fine without disruptions .   
dp6rdz-5-2                                                                        I would n't do anything that could be a choking hazard like Snickers , m&Ms , Smarties etc .   
98xghs-1-3                                                                                                    You do n't actually have to tell her anything of any substance .   

             Post.ID Reply.ID Sent.Num  \
ID                                       
a8v90n-3-4    a8v90n        3        4   
bp0iek-2-2    bp0iek        2        2   
4xv4lf-2-2    4xv4lf        2        2   
dp6rdz-1.1-2  dp6rdz        1        2   
be9axi-3-0    be9axi        3        0   
...              ...      ...      ...   
8kic2y-3-0    8kic2y        3        0   
844azw-1-3    844azw        1        3   
a8v90n-5-3    a8v90n        5        3   
dp6rdz-5-2    dp6rdz        5        2   
98xghs-1-3    98xghs        1        3   

                                                                                                                                                                                                                                                                                                                                                                                                    Question  \
ID                                                                                                                                                                                                           

In [ ]:
# delrem = dev.copy()
# delrem['Reply'] = delrem.index.map(lambda x: find_reply(x, dev))
# delrem = delrem.reset_index()
# delrem = delrem.loc[delrem['Question'].str.contains('\[deleted\]') | delrem['Question'].str.contains('\[removed\]'), ['Question', 'Reply']]
# delrem.sample(10)

## Model loading

In [32]:
saved_model = '../../saved_pretrained/classifier_askparents_bert_dropout:0.1_lr_tr:1e-05_lr_cl:1e-05_wd:0_batch:32_finetune:True_query:True_context:False_seed:45_multigpu:True_labels:ds_frac:1/'

tokenizer = AutoTokenizer.from_pretrained(saved_model)
model = AutoModelForSequenceClassification.from_pretrained(saved_model)

model.eval()

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(28996, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, element

In [33]:
def predict(sequence):
    '''
        Returns classification value - 0,1 given sentence
    '''
    
    x = tokenizer.encode_plus(sequence[0], sequence[1], return_tensors='pt', add_special_tokens=True, return_token_type_ids=True)
    input_ids = x['input_ids']
    token_type_ids = x['token_type_ids']
    with torch.no_grad():
        logits = model(input_ids, token_type_ids=token_type_ids)[0]
    print(logits)

In [34]:
print(dev.loc['98xghs-1-3','Sentence'],"\nContext:", dev.loc['98xghs-1-3','Context'], "\nQuestion:", dev.loc['98xghs-1-3','Question'])

You do n't actually have to tell her anything of any substance . 
Context: She 's got nothing to shit on , so she 'll get bored and move on . They just shit all over everything good in your life . You : Really good . Start ' grey rocking ' her . Sometimes people can never be happy for anyone . Give her a big sentence that does n't say anything . You said a lot , but nothing specific . I 've gotten a lot of great feedback on this project we 're working on . See ? I think a more intimate discussion about this issue would be healthier . How 's things with ( whatever is relevant to change subject , dad / brother / aunt / house ) ? We 'll be done by the end of the quarter ! I 'd just minimize contact with them . Mom : How 's your new job ? It is his mother and it does n’t sound like she deserves to be cut off . 
Question:  The end Rant over, thank you all  Why is my Mother so negative over my new job?


In [35]:
sequence = (dev.loc['98xghs-1-3','Sentence'], dev.loc['98xghs-1-3','Question'])

In [36]:
predict(sequence)

tensor([[ 0.4326, -0.7567]])


## Attention Heads View

In [37]:
def show_head_view(model, tokenizer, sentence_a, sentence_b=None):
    inputs = tokenizer.encode_plus(sentence_a, sentence_b, return_tensors='pt', add_special_tokens=True, return_token_type_ids=True)
    input_ids = inputs['input_ids']
    if sentence_b:
        token_type_ids = inputs['token_type_ids']
        with torch.no_grad():
            attention = model(input_ids, token_type_ids=token_type_ids)[-1]
        sentence_b_start = token_type_ids[0].tolist().index(1)
    else:
        with torch.no_grad():
            attention = model(input_ids)[-1]
        sentence_b_start = None
    input_id_list = input_ids[0].tolist() # Batch index 0
    tokens = tokenizer.convert_ids_to_tokens(input_id_list)    
    head_view(attention, tokens, sentence_b_start)

In [38]:
sentence = dev.loc['98xghs-1-3','Sentence']
context = dev.loc['98xghs-1-3','Question']

In [39]:
show_head_view(model, tokenizer, sentence_a=sentence, sentence_b=context)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
from sklearn.metrics import classification_report
print(classification_report(dev['DS_Label'], dev['Pred_Label']))